In [69]:
import numpy as np
import pandas as pd
import math



In [70]:
df=pd.read_csv("data3_19.csv")

In [71]:
print(df)

     pclass    age  gender survived
0       1st  adult    male      yes
1       1st  adult    male      yes
2       1st  adult    male      yes
3       1st  adult    male      yes
4       1st  adult    male      yes
5       1st  adult    male      yes
6       1st  adult    male      yes
7       1st  adult    male      yes
8       1st  adult    male      yes
9       1st  adult    male      yes
10      1st  adult    male      yes
11      1st  adult    male      yes
12      1st  adult    male      yes
13      1st  adult    male      yes
14      1st  adult    male      yes
15      1st  adult    male      yes
16      1st  adult    male      yes
17      1st  adult    male      yes
18      1st  adult    male      yes
19      1st  adult    male      yes
20      1st  adult    male      yes
21      1st  adult    male      yes
22      1st  adult    male      yes
23      1st  adult    male      yes
24      1st  adult    male      yes
25      1st  adult    male      yes
26      1st  adult    male  

In [72]:
class Node:
    def __init__(self):
        self.attr=""
        self.class_val=""
        self.child_nodes=[]
    
    

In [73]:
def log2(x):
    return math.log(x)/math.log(2)
def pos_neg_count(df):
    num_rows=len(df.axes[0])
    num_cols=len(df.axes[1])-1#neglecting the class column
    
    pos_df=df[df["survived"]=="yes"]
    pos_count=len(pos_df.axes[0])
    neg_count=num_rows-pos_count
    return pos_count,neg_count
def entropy(pos,neg,num_rows):
    if(pos==0 or neg==0):
        return 0
    pos_pr=pos/num_rows
    neg_pr=neg/num_rows
    E=-pos_pr*log2(pos_pr)-neg_pr*log2(neg_pr)
    return E

In [74]:

def form_tree(df,nd,attr_list,level,print_flag):
   
    #print("ATTR LIST = "+str(attr_list))
    #df = dataframe
    #nd=Current Node
    
    #print(df["survived"].unique()) //Two classes = "yes" and "no"
    num_rows=len(df.axes[0])
    num_cols=len(df.axes[1])-1#neglecting the class column
    pos,neg=pos_neg_count(df)
    
    t="\t"*level
    if(pos==0):
        nd.class_val="no"
        if(print_flag==1): print(t+"##Class = no")
        
        return nd
    if(neg==0):
        nd.class_val="yes"
        if(print_flag==1): print(t+"##Class = yes")
        return nd
    
    
    #Finding Prior Entropy
    E1=entropy(pos,neg,num_rows)
    #print(E1)
    #E1==prior Entropy
    
    max_attr=""
    max_diff=-99999
    #Finding Posterior Entropy
    for c in attr_list:
        u=list(df[c].unique())
        if(len(u)==1):
            attr_list.remove(c)
            continue
        else:
            E2=0
            for val in u:
                dfv=df[df[c]==val]
                num_rowsv=len(dfv.axes[0])
                posv,negv=pos_neg_count(dfv)
                E=entropy(posv,negv,num_rowsv)
                E2=E2+num_rowsv*1.0*E/num_rows
            Ediff=E1-E2
            if(Ediff>max_diff):
                max_diff=Ediff
                max_attr=c
                
    
    if(max_diff!=-99999):
        #If a attribute is Chosen, we create child nodes and recursively call function on them
        nd.attr=max_attr
        attr_list.remove(nd.attr)
        u=list(df[max_attr].unique())
        for val in u:
            df1=df[df[max_attr]==val]
            
            if(print_flag==1): print(t+"##"+max_attr+" = "+str(val))
            RN=Node()
            nd.child_nodes.append([val,RN])
            form_tree(df1,RN,attr_list,level+1,print_flag)
        attr_list.append(nd.attr)
        return nd
    else:
        #If no more attribute to choose, then we assign class as majority class
        if(pos>=neg):
            nd.class_val="yes"
            if(print_flag==1): print(t+"##Class = yes")
            return nd
        else:
            nd.class_val="no"
            if(print_flag==1): print(t+"##Class = no")
            return nd
            
        
            
            
    
            
            
                
    

In [79]:
def form_dec_tree(df,print_flag):
    columns=list(df.columns)
    attr_list=columns[0:len(columns)-1] # attr_list = possible attributes to choose from
    RN=Node() # Node created for root node
    RN=form_tree(df,RN,attr_list,0,print_flag)
    return RN
def predict(df,row,tree):
    node=tree
    #print(r)
    #print("\n\n")
    index=0
    while(node.class_val==""):
        print("    PREDICTION INDEX = "+str(index))
        index+=1
        attr=node.attr
        val=df.at[row,attr]
        for l in node.child_nodes:
            if(l[0]==val):
                node=l[1]
    return node.class_val
    
    

    
    
#tree=form_dec_tree(df,1)
#print(list(df.iloc[1]))
#predict(df,1,tree)

In [80]:
def AdaBoost_train(df):
    
    #Will return list of classifiers in the form [ (Tree object 1,alpha 1),   (Tree object 2,alpha 2),...]
    num_rows=len(df.axes[0])
    classifiers=[] # will be of the form classifiers=[[Tree1,Alpha1],[Tree2,Alpha2],[Tree3,Alpha3]]
    weight_rows=np.ones(num_rows)
    weight_rows=weight_rows/num_rows
    for i in range(0,3):
        Tree=form_dec_tree(df,0)
        #print(df.iloc[0])
        target=[[predict(df,int(row),Tree),df.at[row,"survived"]] for row in df.index]
        #each element of target = [predicted class,actual class]
        #print(target)
        eq=[(target[r][0]==target[r][1])*1 for r in range(0,num_rows)]
        acc=sum(eq)*100.0/num_rows
        #print("Classifier "+str(i+1)+" trained with accuracy "+str(acc))
        rows=[index for index,value in enumerate(eq) if value==0] # Misclassified rows
        mis_weights=[weight_rows[r] for r in rows] # Weights of misclassified rows
        error_rate=(sum(mis_weights)*1.0+1*math.exp(-6))/num_rows
        alpha=0.5*math.log((1-error_rate)/(error_rate*1.0))
        classifiers.append([Tree,alpha])
        #print("Classifier "+str(i+1)+" has error rate,alpha = "+str(error_rate)+","+str(alpha))
        
        
        #print(pos_neg_count(df))
        if(i<2):
            for j in range(0,num_rows):
                if(eq[j]==1):#Correctly Classified
                    weight_rows[j]=weight_rows[j]*math.exp(-alpha)
                else:
                    weight_rows[j]=weight_rows[j]*math.exp(alpha)
            weight_rows=weight_rows*1.0/np.sum(weight_rows)
            df=df.sample(num_rows,replace=True,axis=0,weights=weight_rows)
            df=df.reset_index(drop=True)
        
        #print(df)
       
        #print(pos_neg_count(df))
        #print(df)
     
        
        
    #print(weight_rows)
    
    
    
    return classifiers

In [81]:
def predict_test(df,trees):
    #print(trees)
    print("HELLO")
    pred=[]
    for row in df.index:
        print("PREDICTING ROW "+str(row))
        pred.append([predict(df,int(row),trees[0][0]),predict(df,int(row),trees[1][0]),predict(df,int(row),trees[2][0])])
    print("HELLO2")
    alphas=[trees[i][1] for i in range(0,3)]
    print(alphas)
    new_pred=[]
    for row in df.index:
        pred_row=pred[row]
        sum_yes=0
        sum_no=0
        for i in range(0,3):
            if pred_row[i]=="yes":
                sum_yes+=alphas[i]
            elif pred_row[i]=="no":
                sum_no+=alphas[i]
        print(pred_row)
        print(alphas)
        print(sum_yes,sum_no)
        print("\n")
        if(sum_yes>=sum_no):
            new_pred.append("yes")
        else:
            new_pred.append("no")
    tar=[[new_pred[r],df.at[r,"survived"]] for r in df.index]
    eq=[(tar[r][0]==tar[r][1])*1 for r in df.index]
    print(sum(eq),len(df.index))
    acc=sum(eq)*100.0/len(df.index)
    print(acc)
    #print(tar)
    
        
    #pred is of the form [class prediction for first tree, for 2nd, for 3rd]
    #print(pred)
    
   
    
        
    

In [82]:
def main():
    df=pd.read_csv("data3_19.csv")
    cols=df.columns
    Classifiers=AdaBoost_train(df)
    #print(Classifiers)
    df_test=pd.read_csv("test3_19.csv",names=cols)
    acc=predict_test(df_test,Classifiers)

if __name__=="__main__":
    main()
    
    

    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0


    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0


    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 2
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1


    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0


    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1
    PREDICTION INDEX = 0
    PREDICTION INDEX = 1


...

    PREDICTION INDEX = 159563
    PREDICTION INDEX = 159564
    PREDICTION INDEX = 159565
    PREDICTION INDEX = 159566
    PREDICTION INDEX = 159567
    PREDICTION INDEX = 159568
    PREDICTION INDEX = 159569
    PREDICTION INDEX = 159570
    PREDICTION INDEX = 159571
    PREDICTION INDEX = 159572
    PREDICTION INDEX = 159573
    PREDICTION INDEX = 159574
    PREDICTION INDEX = 159575
    PREDICTION INDEX = 159576
    PREDICTION INDEX = 159577
    PREDICTION INDEX = 159578
    PREDICTION INDEX = 159579
    PREDICTION INDEX = 159580
    PREDICTION INDEX = 159581
    PREDICTION INDEX = 159582
    PREDICTION INDEX = 159583
    PREDICTION INDEX = 159584
    PREDICTION INDEX = 159585
    PREDICTION INDEX = 159586
    PREDICTION INDEX = 159587
    PREDICTION INDEX = 159588
    PREDICTION INDEX = 159589
    PREDICTION INDEX = 159590
    PREDICTION INDEX = 159591
    PREDICTION INDEX = 159592
    PREDICTION INDEX = 159593
    PREDICTION INDEX = 159594
    PREDICTION INDEX = 159595
    PREDIC

    PREDICTION INDEX = 160736
    PREDICTION INDEX = 160737
    PREDICTION INDEX = 160738
    PREDICTION INDEX = 160739
    PREDICTION INDEX = 160740
    PREDICTION INDEX = 160741
    PREDICTION INDEX = 160742
    PREDICTION INDEX = 160743
    PREDICTION INDEX = 160744
    PREDICTION INDEX = 160745
    PREDICTION INDEX = 160746
    PREDICTION INDEX = 160747
    PREDICTION INDEX = 160748
    PREDICTION INDEX = 160749
    PREDICTION INDEX = 160750
    PREDICTION INDEX = 160751
    PREDICTION INDEX = 160752
    PREDICTION INDEX = 160753
    PREDICTION INDEX = 160754
    PREDICTION INDEX = 160755
    PREDICTION INDEX = 160756
    PREDICTION INDEX = 160757
    PREDICTION INDEX = 160758
    PREDICTION INDEX = 160759
    PREDICTION INDEX = 160760
    PREDICTION INDEX = 160761
    PREDICTION INDEX = 160762
    PREDICTION INDEX = 160763
    PREDICTION INDEX = 160764
    PREDICTION INDEX = 160765
    PREDICTION INDEX = 160766
    PREDICTION INDEX = 160767
    PREDICTION INDEX = 160768
    PREDIC

    PREDICTION INDEX = 161919
    PREDICTION INDEX = 161920
    PREDICTION INDEX = 161921
    PREDICTION INDEX = 161922
    PREDICTION INDEX = 161923
    PREDICTION INDEX = 161924
    PREDICTION INDEX = 161925
    PREDICTION INDEX = 161926
    PREDICTION INDEX = 161927
    PREDICTION INDEX = 161928
    PREDICTION INDEX = 161929
    PREDICTION INDEX = 161930
    PREDICTION INDEX = 161931
    PREDICTION INDEX = 161932
    PREDICTION INDEX = 161933
    PREDICTION INDEX = 161934
    PREDICTION INDEX = 161935
    PREDICTION INDEX = 161936
    PREDICTION INDEX = 161937
    PREDICTION INDEX = 161938
    PREDICTION INDEX = 161939
    PREDICTION INDEX = 161940
    PREDICTION INDEX = 161941
    PREDICTION INDEX = 161942
    PREDICTION INDEX = 161943
    PREDICTION INDEX = 161944
    PREDICTION INDEX = 161945
    PREDICTION INDEX = 161946
    PREDICTION INDEX = 161947
    PREDICTION INDEX = 161948
    PREDICTION INDEX = 161949
    PREDICTION INDEX = 161950
    PREDICTION INDEX = 161951
    PREDIC

    PREDICTION INDEX = 162993
    PREDICTION INDEX = 162994
    PREDICTION INDEX = 162995
    PREDICTION INDEX = 162996
    PREDICTION INDEX = 162997
    PREDICTION INDEX = 162998
    PREDICTION INDEX = 162999
    PREDICTION INDEX = 163000
    PREDICTION INDEX = 163001
    PREDICTION INDEX = 163002
    PREDICTION INDEX = 163003
    PREDICTION INDEX = 163004
    PREDICTION INDEX = 163005
    PREDICTION INDEX = 163006
    PREDICTION INDEX = 163007
    PREDICTION INDEX = 163008
    PREDICTION INDEX = 163009
    PREDICTION INDEX = 163010
    PREDICTION INDEX = 163011
    PREDICTION INDEX = 163012
    PREDICTION INDEX = 163013
    PREDICTION INDEX = 163014
    PREDICTION INDEX = 163015
    PREDICTION INDEX = 163016
    PREDICTION INDEX = 163017
    PREDICTION INDEX = 163018
    PREDICTION INDEX = 163019
    PREDICTION INDEX = 163020
    PREDICTION INDEX = 163021
    PREDICTION INDEX = 163022
    PREDICTION INDEX = 163023
    PREDICTION INDEX = 163024
    PREDICTION INDEX = 163025
    PREDIC

KeyboardInterrupt: 